#### Import relevant libraries

In [0]:
from pyspark.sql.types import *
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, concat_ws, collect_list, monotonically_increasing_id; import pyspark.sql.functions as F



create spark session

In [0]:
spark = SparkSession.builder.getOrCreate()

Load databases

In [0]:
companies = spark.read.parquet('/dbfs/linkedin_train_data')
profiles = spark.read.parquet('/dbfs/linkedin_people_train_data')

In [0]:
display(profiles)

about avatar certifications city country_code current_company current_company:company_id current_company:name education educations_details experience followers following groups id languages name people_also_viewed position posts recommendations recommendations_count timestamp url volunteer_experience сourses null https://media.licdn.com/dms/image/C4D03AQE-B0QzjS1Cgw/profile-displayphoto-shrink_800_800/0/1517524530883?e=2147483647&v=beta&t=xKHfKdT1DZxpZWl18-G7N7gjacJaqkxBJ6v-JzxXXEo List() Holland, Michigan, United States US List(null, Michigan Conference of the United Methodist Church, null, Michigan Conference of the United Methodist Church, retired at Michigan Conference of the United Methodist Church) null Michigan Conference of the United Methodist Church List() null List(List(null, null, null, Jun 1992 - Present 31 years 4 months, 31 years 4 months, Present, null, null, Jun 1992, Michigan Conference of the United Methodist Church, null, retired, null)) 76 76 List() glenn-wagner-366824138 List() Glenn Wagner List(List(https://www.linkedin.com/in/gerald-allison-b9b78080?trk=public_profile_browsemap), List(https://www.linkedin.com/in/mzammit08?trk=public_profile_browsemap), List(https://au.linkedin.com/in/mikezammitmelbaus?trk=public_profile_browsemap), List(https://au.linkedin.com/in/mike-zammit-cima%C2%AE-07a1123a?trk=public_profile_browsemap), List(https://ca.linkedin.com/in/michael-zammit-573b2261?trk=public_profile_browsemap), List(https://www.linkedin.com/in/phil-jones-29018a13?trk=public_profile_browsemap), List(https://www.linkedin.com/in/al-trucano-27954955?trk=public_profile_browsemap), List(https://www.linkedin.com/in/sharon-cress-b0814690?trk=public_profile_browsemap), List(https://www.linkedin.com/in/ron-bentzinger-327a35177?trk=public_profile_browsemap), List(https://www.linkedin.com/in/eloise-saltzgaver-48a08668?trk=public_profile_browsemap), List(https://www.linkedin.com/in/george-klohck-33b38597?trk=public_profile_browsemap), List(https://www.linkedin.com/in/dennis-shaw-92087017?trk=public_profile_browsemap), List(https://www.linkedin.com/in/james-kayler-bb9556a1?trk=public_profile_browsemap), List(https://www.linkedin.com/in/sue-ann-salmon-60a16433?trk=public_profile_browsemap), List(https://www.linkedin.com/in/gordon-packard-6777a591?trk=public_profile_browsemap), List(https://www.linkedin.com/in/loy-lilley-90b27758?trk=public_profile_browsemap), List(https://www.linkedin.com/in/john-mcfarlane-2a8376114?trk=public_profile_browsemap), List(https://www.linkedin.com/in/duane-mevis-b66a6128?trk=public_profile_browsemap), List(https://www.linkedin.com/in/george-white-054a6b42?trk=public_profile_browsemap), List(https://www.linkedin.com/in/jane-wood-37a18a79?trk=public_profile_browsemap)) retired at Michigan Conference of the United Methodist Church List() List() null 2023-09-04 https://www.linkedin.com/in/glenn-wagner-366824138 List() List() null https://media.licdn.com/dms/image/C4D03AQE-F_SOngHmkA/profile-displayphoto-shrink_800_800/0/1618610169232?e=2147483647&v=beta&t=Xg7mvCdrJbKYJS51k8xxUHXINN4WitaI6kAh1-SqlN8 List() Topeka, Kansas, United States US List(bcbsks, Blue Cross and Blue Shield of Kansas, https://my.linkedin.com/company/bcbsks?trk=public_profile_topcard-current-company, Blue Cross and Blue Shield of Kansas, IT Infrastructure Administrator) bcbsks Blue Cross and Blue Shield of Kansas List() null List(List(null, null, null, Aug 2022 - Present 1 year 2 months, 1 year 2 months, Present, Topeka, Kansas, United States, null, Aug 2022, Blue Cross and Blue Shield of Kansas, https://my.linkedin.com/company/bcbsks?trk=public_profile_experience-item_profile-section-card_subtitle-click, System Administrator, null), List(Cerner Corporation, cerner-corporation, null, 5 years 2 months, null, null, null, List(List(null, Jun 2021 Aug 2022 1 year 3 months, 1 year 3 months, Aug 2022, Jun 2021 - Aug 20221 year 3 months , Kansas City, Missouri, United States, Jun 2021, Cerner Corporation, Production Owner), List(nul

In [0]:
profiles.printSchema()

root
 |-- about: string (nullable = true)
 |-- avatar: string (nullable = true)
 |-- certifications: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- meta: string (nullable = true)
 |    |    |-- subtitle: string (nullable = true)
 |    |    |-- title: string (nullable = true)
 |-- city: string (nullable = true)
 |-- country_code: string (nullable = true)
 |-- current_company: struct (nullable = true)
 |    |-- company_id: string (nullable = true)
 |    |-- industry: string (nullable = true)
 |    |-- link: string (nullable = true)
 |    |-- name: string (nullable = true)
 |    |-- title: string (nullable = true)
 |-- current_company:company_id: string (nullable = true)
 |-- current_company:name: string (nullable = true)
 |-- education: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- degree: string (nullable = true)
 |    |    |-- end_year: string (nullable = true)
 |    |    |-- field: string (nullable = true

#### Aggregate all positions' inforamtion

In [0]:
profile_experience_explode = profiles.withColumn(
    "experience_explode", F.explode("experience")
).filter(
    (F.col("experience_explode.description").isNotNull()) |
    (F.col("experience_explode.positions").isNotNull())
)

profile_experience_positions_explode = profile_experience_explode.withColumn("positions_explode", F.explode("experience_explode.positions"))


profile_experience_positions_explode = profile_experience_positions_explode.withColumn("Company_Name",F.col("experience_explode.company"))\
                                                                           .withColumn("Position_Description", F.col("positions_explode.description"))\
                                                                           .withColumn("Position_Title", F.col("positions_explode.title"))

profile_experience_positions_explode = profile_experience_positions_explode.select("id",
                                                                                   "experience",
                                                                                   "experience_explode",
                                                                                   "Position_Description",
                                                                                   "Position_Title")



profile_experience_positions_null = profile_experience_explode.filter(
    (F.col("experience_explode.description").isNotNull()))

"""profile_experience_positions_null.withColumn("Company_Name",F.col("experience_explode.company"))\
                                 .withColumn("Position_Description", F.col("experience_explode.description"))\
                                 .withColumn("Position_Title", F.col("experience_explode.title"))"""


profile_experience_positions_null = profile_experience_positions_null.withColumn(
    "Company_Name", F.col("experience_explode.company"))\
        .withColumn("Position_Description", F.col("experience_explode.description"))\
            .withColumn("Position_Title", F.col("experience_explode.title"))

profile_experience_positions_null = profile_experience_positions_null.select(
    "id",
    "experience",
    "experience_explode",
    "Position_Description",
    "Position_Title"
)



Merge the different df's

In [0]:
merged_df = profile_experience_positions_explode.unionByName(profile_experience_positions_null)
merged_df.count()

3259733

In [0]:
display(merged_df)

id experience experience_explode Position_Description Position_Title stephen-hockenbarger-494128210 List(List(null, null, null, Aug 2022 - Present 1 year 2 months, 1 year 2 months, Present, Topeka, Kansas, United States, null, Aug 2022, Blue Cross and Blue Shield of Kansas, https://my.linkedin.com/company/bcbsks?trk=public_profile_experience-item_profile-section-card_subtitle-click, System Administrator, null), List(Cerner Corporation, cerner-corporation, null, 5 years 2 months, null, null, null, List(List(null, Jun 2021 Aug 2022 1 year 3 months, 1 year 3 months, Aug 2022, Jun 2021 - Aug 20221 year 3 months , Kansas City, Missouri, United States, Jun 2021, Cerner Corporation, Production Owner), List(null, Jul 2017 Aug 2022 5 years 2 months, 5 years 2 months, Aug 2022, Jul 2017 - Aug 20225 years 2 months, Jul 2017, Cerner Corporation, Senior System Engineer)), null, null, null, null, https://my.linkedin.com/company/cerner-corporation?trk=public_profile_experience-group-header)) List(Cerner Corporation, cerner-corporation, null, 5 years 2 months, null, null, null, List(List(null, Jun 2021 Aug 2022 1 year 3 months, 1 year 3 months, Aug 2022, Jun 2021 - Aug 20221 year 3 months , Kansas City, Missouri, United States, Jun 2021, Cerner Corporation, Production Owner), List(null, Jul 2017 Aug 2022 5 years 2 months, 5 years 2 months, Aug 2022, Jul 2017 - Aug 20225 years 2 months, Jul 2017, Cerner Corporation, Senior System Engineer)), null, null, null, null, https://my.linkedin.com/company/cerner-corporation?trk=public_profile_experience-group-header) null Production Owner stephen-hockenbarger-494128210 List(List(null, null, null, Aug 2022 - Present 1 year 2 months, 1 year 2 months, Present, Topeka, Kansas, United States, null, Aug 2022, Blue Cross and Blue Shield of Kansas, https://my.linkedin.com/company/bcbsks?trk=public_profile_experience-item_profile-section-card_subtitle-click, System Administrator, null), List(Cerner Corporation, cerner-corporation, null, 5 years 2 months, null, null, null, List(List(null, Jun 2021 Aug 2022 1 year 3 months, 1 year 3 months, Aug 2022, Jun 2021 - Aug 20221 year 3 months , Kansas City, Missouri, United States, Jun 2021, Cerner Corporation, Production Owner), List(null, Jul 2017 Aug 2022 5 years 2 months, 5 years 2 months, Aug 2022, Jul 2017 - Aug 20225 years 2 months, Jul 2017, Cerner Corporation, Senior System Engineer)), null, null, null, null, https://my.linkedin.com/company/cerner-corporation?trk=public_profile_experience-group-header)) List(Cerner Corporation, cerner-corporation, null, 5 years 2 months, null, null, null, List(List(null, Jun 2021 Aug 2022 1 year 3 months, 1 year 3 months, Aug 2022, Jun 2021 - Aug 20221 year 3 months , Kansas City, Missouri, United States, Jun 2021, Cerner Corporation, Production Owner), List(null, Jul 2017 Aug 2022 5 years 2 months, 5 years 2 months, Aug 2022, Jul 2017 - Aug 20225 years 2 months, Jul 2017, Cerner Corporation, Senior System Engineer)), null, null, null, null, https://my.linkedin.com/company/cerner-corporation?trk=public_profile_experience-group-header) null Senior System Engineer megan-dorsey-7ab6a9167 List(List(Fat Beet Farm, fat-beet-farm, null, 2 years 2 months, null, null, null, List(List(null, Dec 2021 - Present 1 year 10 months, 1 year 10 months, Present, Dec 2021 - Present1 year 10 months , Tampa, Florida, United States, Dec 2021, Fat Beet Farm, Microgreens Manager), List(null, Aug 2021 Dec 2021 5 months, 5 months, Dec 2021, Aug 2021 - Dec 20215 months , Tampa, Florida, United States, Aug 2021, Fat Beet Farm, Aquaponics and Micro-Green Growing Intern)), null, null, null, null, https://www.linkedin.com/company/fat-beet-farm?trk=public_profile_experience-group-header), List(null, null, null, Sep 2021 May 2023 1 year 9 months, 1 year 9 months, May 2023, Tampa, Florida, United States, null, Sep 2021, Soccer Shots Franchising, https://www.linkedin.com/company/soccer-shots?trk=public_profile_experience-item_profile-section-card_subtitle-click, S

In [0]:
unique_ids_count = merged_df.select("id").distinct().count()
print(f"Number of unique IDs: {unique_ids_count}")

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:445)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperation$1(UsageLogging.scala:528)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:633)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:656)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:276)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(Attr

In [0]:
merged_df.printSchema()

root
 |-- id: string (nullable = true)
 |-- experience: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- company: string (nullable = true)
 |    |    |-- company_id: string (nullable = true)
 |    |    |-- description: string (nullable = true)
 |    |    |-- duration: string (nullable = true)
 |    |    |-- duration_short: string (nullable = true)
 |    |    |-- end_date: string (nullable = true)
 |    |    |-- location: string (nullable = true)
 |    |    |-- positions: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- description: string (nullable = true)
 |    |    |    |    |-- duration: string (nullable = true)
 |    |    |    |    |-- duration_short: string (nullable = true)
 |    |    |    |    |-- end_date: string (nullable = true)
 |    |    |    |    |-- meta: string (nullable = true)
 |    |    |    |    |-- start_date: string (nullable = true)
 |    |    |    |    |-- subtitle: st

In [0]:

# Concatenate Position_Title and Position_Description
merged_concat_position = merged_df.withColumn(
    "position_concat", 
    concat_ws(": ", col("Position_Title"), col("Position_Description"))
)

merged_concat_position = merged_concat_position.select("id",
                                                       "experience",
                                                       "experience_explode",
                                                       "Position_concat")



# Group by id and aggregate the new column with a delimiter (e.g., "\n")
concat_position_for_id = merged_concat_position.groupBy("id").agg(
    concat_ws("\n", collect_list("position_concat")).alias("aggregated_positions")
)

display(concat_position_for_id)

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:445)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperation$1(UsageLogging.scala:528)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:633)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:656)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:276)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(Attr

In [0]:
concat_position_for_id.count()

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:445)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperation$1(UsageLogging.scala:528)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:633)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:656)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:276)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(Attr

In [0]:
disploredered_companies = companies.orderBy(companies.followers.desc())

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:445)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperation$1(UsageLogging.scala:528)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:633)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:656)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:276)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(Attr

In [0]:
# Add an index column (monotonically increasing, not consecutive)
df_with_index = oredered_companies.withColumn("index", monotonically_increasing_id())

# Filter rows between 3001 and 6000
result = df_with_index.filter((col("index") >= 3000) & (col("index") < 6000))

# Select the "name" column from the DataFrame
display(result.select("name"))

com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:445)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.cancelExecution(ExecutionContextManagerV1.scala:464)
	at com.databricks.spark.chauffeur.ChauffeurState.$anonfun$process$1(ChauffeurState.scala:571)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperation$1(UsageLogging.scala:528)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:633)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:656)
	at com.databricks.logging.AttributionContextTracing.$anonfun$withAttributionContext$1(AttributionContextTracing.scala:48)
	at com.databricks.logging.AttributionContext$.$anonfun$withValue$1(AttributionContext.scala:276)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(Attr